In [59]:
%pip install --upgrade requests
%pip install jieba
%pip install pypinyin
%pip install -v torch torchtext --index-url https://download.pytorch.org/whl/cu118
%pip install chardet
%pip install transformers
%pip install ipywidgets
%pip install --upgrade jupyter_core jupyter_client
%pip install pandas
%pip install re
%pip install scikit-learn
%pip install scipy==1.10.1
%pip install gensim

Using pip 23.1.2 from /usr/local/lib/python3.10/dist-packages/pip (python 3.10)
Looking in indexes: https://download.pytorch.org/whl/cu118
  Using cached jupyter_client-7.4.9-py3-none-any.whl (133 kB)
  Attempting uninstall: jupyter-client
    Found existing installation: jupyter_client 8.6.2
    Uninstalling jupyter_client-8.6.2:
      Successfully uninstalled jupyter_client-8.6.2
  Using cached jupyter_client-8.6.2-py3-none-any.whl (105 kB)
  Attempting uninstall: jupyter_client
    Found existing installation: jupyter_client 7.4.9
    Uninstalling jupyter_client-7.4.9:
      Successfully uninstalled jupyter_client-7.4.9
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
notebook 6.5.5 requires jupyter-client<8,>=5.3.4, but you have jupyter-client 8.6.2 which is incompatible.
ERROR: Could not find a version that satisfies the requirement re (from versions: none)

In [60]:
!jupyter nbextension enable --py widgetsnbextension
import jieba
import pypinyin
import torch
from transformers import AutoTokenizer, AutoModel
import pandas
import re
from sklearn.model_selection import train_test_split
from sklearn.datasets import load_iris
import numpy

Enabling notebook extension jupyter-js-widgets/extension...
Paths used for configuration of notebook: 
    	/root/.jupyter/nbconfig/notebook.json
Paths used for configuration of notebook: 
    	
      - Validating: OK
Paths used for configuration of notebook: 
    	/root/.jupyter/nbconfig/notebook.json


In [61]:
print(torch.cuda.is_available())
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

True


## Normalizacja wejścia - pozbycie się spacji i znaków innych niż chińskie (interpunkcyjnych).
### TODO - przepisać używając słownika znaków chińskich?

In [62]:
# lower() - male litery
# strip() - bez krancowych znakow niedrukowalnych
# bez znakow interpunkcyjnych
def normalizeString(s):
    s = s.lower().strip()
    s = re.sub(r"([.!?])", r"", s)
    s = re.sub(r"([,;:-])", r"", s)
    s = re.sub(r"([。，？”“《》·、！：；π…ㄚ])", r"", s)
    s = re.sub(r"([/])", r"", s)
    s = re.sub(r"(['\"])", r" ", s)
    return s.strip()

def normalizeChinese(s):
    s = normalizeString(s)
    pom = ""
    for c in s:
        if c != " ":
            pom+=c
        #pom+=" "
    return pom.strip()

## Wczytanie zbioru danych. https://www.kaggle.com/datasets/marquis03/chinese-couplets-dataset

In [63]:
fixed_couplets_in = pandas.read_csv("fixed_couplets_in.txt", sep="\t", names=["in"], header=None)
fixed_couplets_out = pandas.read_csv("fixed_couplets_out.txt", sep="\t", names=["out"], header=None)

normalized_fixed_couplets_in=[]
for _ in fixed_couplets_in["in"]:
    normalized_fixed_couplets_in.append(normalizeChinese(_))
normalized_fixed_couplets_out=[]
for _ in fixed_couplets_out["out"]:
    normalized_fixed_couplets_out.append(normalizeChinese(_))

print(normalized_fixed_couplets_in[0])
print(normalized_fixed_couplets_out[0])

腾飞上铁锐意改革谋发展勇当千里马
和谐南供安全送电保畅通争做领头羊


In [64]:
fixed_couplets = pandas.DataFrame(
    {"in": normalized_fixed_couplets_in,
     "out": normalized_fixed_couplets_out
    }
    )
print(fixed_couplets)

                      in               out
0       腾飞上铁锐意改革谋发展勇当千里马  和谐南供安全送电保畅通争做领头羊
1                风弦未拨心先乱           夜幕已沉梦更闲
2                花梦粘于春袖口           莺声溅落柳枝头
3                晋世文章昌二陆           魏家词赋重三曹
4                一句相思吟岁月           千杯美酒醉风情
...                  ...               ...
744910           半榻诗书盈陋室           一墙字画靓寒庐
744911           借角青山埋姓字           掬壶明月洗尘心
744912      苑内尽天姿锦窠仙髻无双艳      亭前多国色金粉紫檀第一香
744913         浩淼洞庭极目天为界         安闲钓叟静心孰羡鱼
744914           志踏云梯能揽月           坚磨铁棒可成针

[744915 rows x 2 columns]


### Odrzucenie 99% danych - więcej niż 5% zajmuje całą pamięć i wywala program.
### Podział danych na zbiór treningowy i testowy.

In [65]:
male, duze = train_test_split(fixed_couplets,test_size=0.99,random_state=42)
treningowe, testowe = train_test_split(male,test_size=0.2,random_state=42)
print(treningowe)
print(testowe)

                       in                out
567354              宇高炎暑净              秋爽飒风来
118920              忧乐关天下              安危系一身
738591            一盏相思量寂寞            三分惆怅兑凄凉
509346  孝驻锦绣城喜吕梁歌飞春融三晋千秋画  义圆和谐梦看汾河景瑞水起九州万卷诗
75388             春临八桂海豚舞            福满九州彩凤飞
...                   ...                ...
116492  创中华古老文明当同日月齐辉功垂万代  启黎庶鸿蒙草昧是与山河并寿德颂千秋
91658         纠缠海角指相思何时作罢        浪迹天涯心倦怠哪处归依
101376       特地显英灵化被逢人歌泽渥       配天昭厚德恩深无处不波恬
262048        温暖鹅城展翅奋飞中国梦        祥和蛇岁铺春欢庆小康年
415192       百业一支歌歌伴和风谐雨唱       九江千古梦梦同朗月艳阳圆

[5959 rows x 2 columns]
                in         out
274864     林霭渐浓迷古寺     尘烟已远隐青山
222320     自古青天匡正义     而今华夏振雄风
100260  真心请客就该一五一五  假意为情何必我开我开
435928     爱本有心今不见     人如无欲意何求
446991     欲抹闲愁实不易     谁将片语问何求
...            ...         ...
213030     万象随缘观自在     一心发愿待君归
299155     春联妙句动心魄     小院雅风入彩光
643294     梅亭吹雪横霜笛     松麓邀云放月筝
628861     红似桃花白似雪     绿如李叶亮如霜
566605     数字双音分两用     联文对句限孤平

[1490 rows x 2 columns]


### Przywrócenie numeracji od 0.

In [66]:
treningowe = treningowe.reset_index(drop=True)
testowe = testowe.reset_index(drop=True)
print(treningowe)
print(testowe)

                     in                out
0                 宇高炎暑净              秋爽飒风来
1                 忧乐关天下              安危系一身
2               一盏相思量寂寞            三分惆怅兑凄凉
3     孝驻锦绣城喜吕梁歌飞春融三晋千秋画  义圆和谐梦看汾河景瑞水起九州万卷诗
4               春临八桂海豚舞            福满九州彩凤飞
...                 ...                ...
5954  创中华古老文明当同日月齐辉功垂万代  启黎庶鸿蒙草昧是与山河并寿德颂千秋
5955        纠缠海角指相思何时作罢        浪迹天涯心倦怠哪处归依
5956       特地显英灵化被逢人歌泽渥       配天昭厚德恩深无处不波恬
5957        温暖鹅城展翅奋飞中国梦        祥和蛇岁铺春欢庆小康年
5958       百业一支歌歌伴和风谐雨唱       九江千古梦梦同朗月艳阳圆

[5959 rows x 2 columns]
              in         out
0        林霭渐浓迷古寺     尘烟已远隐青山
1        自古青天匡正义     而今华夏振雄风
2     真心请客就该一五一五  假意为情何必我开我开
3        爱本有心今不见     人如无欲意何求
4        欲抹闲愁实不易     谁将片语问何求
...          ...         ...
1485     万象随缘观自在     一心发愿待君归
1486     春联妙句动心魄     小院雅风入彩光
1487     梅亭吹雪横霜笛     松麓邀云放月筝
1488     红似桃花白似雪     绿如李叶亮如霜
1489     数字双音分两用     联文对句限孤平

[1490 rows x 2 columns]


### Pakiet *pypinyin* przewiduje wymowę pinyin dobrze bez potrzeby używania pakietu *jieba*.

In [67]:
from pypinyin import pinyin, lazy_pinyin, Style

zdanie = treningowe["in"][4]
print(zdanie)
print(pinyin(zdanie, style=Style.TONE3, neutral_tone_with_five=True))
print(lazy_pinyin(zdanie, style=Style.TONE3, neutral_tone_with_five=True))

slowa = list(jieba.cut(zdanie))
print(slowa)
print(pinyin(slowa, style=Style.TONE3, neutral_tone_with_five=True))
print(lazy_pinyin(slowa, style=Style.TONE3, neutral_tone_with_five=True))

春临八桂海豚舞
[['chun1'], ['lin2'], ['ba1'], ['gui4'], ['hai3'], ['tun2'], ['wu3']]
['chun1', 'lin2', 'ba1', 'gui4', 'hai3', 'tun2', 'wu3']
['春临', '八桂', '海豚', '舞']
[['chun1'], ['lin2'], ['ba1'], ['gui4'], ['hai3'], ['tun2'], ['wu3']]
['chun1', 'lin2', 'ba1', 'gui4', 'hai3', 'tun2', 'wu3']


## Podział wymowy pinyin na początki (initials), końcówki (finals) i tony.
### Zamina w liczby przy pomocy słownika.

In [68]:
from pypinyin.contrib.tone_convert import to_finals, to_initials
# 声母表
_INITIALS=['b','p','m','f','d','t','n','l','g','k','h','j','q','x','zh','ch','sh','r','z','c','s',]
# 声母表,把 y,w 也当作声母
_INITIALS_NOT_STRICT=_INITIALS+['y','w']
# 韵母表
_FINALS=['i','u','ü','a','ia','ua','o','uo','e','ie','üe','ai','uai','ei','uei','ao','iao','ou','iou','an','ian','uan','üan','en','in','uen','ün','ang','iang','uang','eng','ing','ueng','ong','iong','er','ê',]

slownik_initials = {}
licznik = 1
for indeks_wersu_pierwszego in _INITIALS+[""]:
    slownik_initials[indeks_wersu_pierwszego] = licznik
    licznik+=1

slownik_finals = {}
licznik = 1
for indeks_wersu_pierwszego in _FINALS+[""]:
    slownik_finals[indeks_wersu_pierwszego] = licznik
    licznik+=1

def poczatek_koniec_ton(zapis_pinyin_3):
    poczatek = slownik_initials[to_initials(zapis_pinyin_3)]
    koniec = slownik_finals[to_finals(zapis_pinyin_3).replace('v', 'ü')]
    ton = int(zapis_pinyin_3[-1])
    return poczatek, koniec, ton

def wymowy_i_tony_zdania(zdanie):
    zapis_pinyin_3_zdania = lazy_pinyin(zdanie, style=Style.TONE3, neutral_tone_with_five=True)
    poczatki = []
    konce =[]
    tony = []
    # print(zdanie, zapis_pinyin_3_zdania)
    for zp3 in zapis_pinyin_3_zdania:
        p,k,t = poczatek_koniec_ton(zp3)
        poczatki.append(p)
        konce.append(k)
        tony.append(t)
    return poczatki, konce, tony

def dopasuj_dlugosc_wektora(wektor, dlugosc_wektora):
    if len(wektor)>dlugosc_wektora:
        wynik = wektor[:dlugosc_wektora]
    else:
        wynik = numpy.pad(wektor,(0,dlugosc_wektora-len(wektor)), mode='constant', constant_values=0)
    return wynik

In [69]:
def poczatki_konce_tony_dla_zdan(zdania, liczba_wejscia):
    poczatki_wyn = []
    konce_wyn = []
    tony_wyn = []

    for zdanie in zdania:
        poczatki, konce, tony = wymowy_i_tony_zdania(zdanie)

        poczatki = dopasuj_dlugosc_wektora(poczatki, liczba_wejscia)
        konce = dopasuj_dlugosc_wektora(konce, liczba_wejscia)
        tony = dopasuj_dlugosc_wektora(tony, liczba_wejscia)

        poczatki_wyn.append(poczatki)
        konce_wyn.append(konce)
        tony_wyn.append(tony)

    return poczatki_wyn, konce_wyn, tony_wyn

### Początki, końcówki i tony wierszy treningowych.

In [70]:
print(len(treningowe["in"]))
print(treningowe["in"][0])
print(treningowe["out"][0])

liczba_wejscia = 35

poczatki_treningowe_in, konce_treningowe_in, tony_treningowe_in = poczatki_konce_tony_dla_zdan(treningowe["in"], liczba_wejscia)
poczatki_treningowe_out, konce_treningowe_out, tony_treningowe_out = poczatki_konce_tony_dla_zdan(treningowe["out"], liczba_wejscia)

print(len(poczatki_treningowe_in))
print(poczatki_treningowe_in[0])
print(konce_treningowe_in[0])
print(tony_treningowe_in[0])
print(poczatki_treningowe_out[0])
print(konce_treningowe_out[0])
print(tony_treningowe_out[0])

5959
宇高炎暑净
秋爽飒风来
5959
[22  9 22 17 12  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[ 3 16 21  2 32  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[3 1 2 3 4 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
[13 17 21  4  8  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[19 30  4 31 12  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[1 3 4 1 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


## Zanurzenia BAAI wierszy treningowych. https://huggingface.co/BAAI/bge-small-zh-v1.5

In [71]:
# Load model from HuggingFace Hub
tokenizer = AutoTokenizer.from_pretrained("BAAI/bge-small-zh-v1.5")
model = AutoModel.from_pretrained("BAAI/bge-small-zh-v1.5")
model.eval()

def zanurzenia_zdan(lista_zdan):
    # Sentences we want sentence embeddings for
    #sentences = ["样例数据-1样例数据", "样例数据-2样例数据"]
    sentences = lista_zdan

    # Tokenize sentences
    encoded_input = tokenizer(sentences, padding=True, truncation=True, return_tensors='pt')
    # for s2p(short query to long passage) retrieval task, add an instruction to query (not add instruction for passages)
    # encoded_input = tokenizer([instruction + q for q in queries], padding=True, truncation=True, return_tensors='pt')

    # Compute token embeddings
    with torch.no_grad():
        model_output = model(**encoded_input)
        # Perform pooling. In this case, cls pooling.
        sentence_embeddings = model_output[0][:, 0]
    # normalize embeddings
    sentence_embeddings = torch.nn.functional.normalize(sentence_embeddings, p=2, dim=1)
    # print("Sentence embeddings shape:", sentence_embeddings.shape)
    # print("Sentence embeddings:", sentence_embeddings)

    return sentence_embeddings

def zanurzenie_zdania(zdanie):
    # Tokenize sentences
    encoded_input = tokenizer(zdanie, padding=True, truncation=True, return_tensors='pt')
    # for s2p(short query to long passage) retrieval task, add an instruction to query (not add instruction for passages)
    # encoded_input = tokenizer([instruction + q for q in queries], padding=True, truncation=True, return_tensors='pt')

    # Compute token embeddings
    with torch.no_grad():
        model_output = model(**encoded_input)
        # Perform pooling. In this case, cls pooling.
        sentence_embedding = model_output[0][:, 0]
    # normalize embeddings
    sentence_embedding = torch.nn.functional.normalize(sentence_embedding, p=2, dim=1)

    return sentence_embedding

In [72]:
treningowe_in_lista = treningowe["in"].tolist()
treningowe_out_lista = treningowe["out"].tolist()

print(len(treningowe_in_lista))
print(treningowe_in_lista[0])
print(treningowe_out_lista[0])

zanurzenia_treningowe_in = zanurzenia_zdan(treningowe_in_lista)
zanurzenia_treningowe_out = zanurzenia_zdan(treningowe_out_lista)

print(zanurzenia_treningowe_in.shape)
print(zanurzenia_treningowe_in[0])
print(zanurzenia_treningowe_out[0])

5959
宇高炎暑净
秋爽飒风来
torch.Size([5959, 512])
tensor([-3.1409e-02,  4.2919e-02, -1.4236e-02,  6.2288e-02, -3.2497e-02,
        -5.3290e-02,  4.7686e-02,  7.7745e-02, -2.0447e-02,  2.8347e-02,
         1.3510e-02, -2.3332e-01,  8.9271e-04,  4.0544e-02,  9.2784e-05,
        -1.1740e-02, -1.6238e-02, -4.7785e-02, -8.7547e-02,  6.0501e-02,
        -1.7588e-02, -4.3948e-03, -3.1034e-02, -8.8176e-03,  3.8507e-02,
        -5.6918e-02,  6.8194e-02,  7.5235e-03,  6.6778e-03,  2.0831e-02,
         9.5349e-04,  4.5033e-02, -9.4392e-03, -3.2470e-02, -3.5810e-02,
        -2.1215e-02, -2.9089e-02,  3.8043e-02, -2.6267e-02,  5.2310e-02,
        -6.3633e-02,  4.2117e-02,  1.7834e-02, -5.5019e-02, -7.9315e-02,
         8.2654e-04, -1.0802e-02,  1.8213e-02,  6.5130e-02, -7.6177e-03,
        -3.8167e-02,  5.3484e-02,  3.5490e-02,  2.7366e-02, -3.0560e-02,
        -7.8364e-02, -3.3920e-02,  7.5826e-03, -1.6268e-02,  1.9344e-02,
         3.4404e-02,  1.1855e-02, -3.5319e-02, -1.1730e-02,  6.7642e-02,
         3

### Tensory - reprezentacje pierwszych wersów wierszy treningowych.

In [73]:
x = []
for indeks_wersu_pierwszego in range(len(zanurzenia_treningowe_in)):
    x.append(torch.cat(
        (
            zanurzenia_treningowe_in[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_treningowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_treningowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_treningowe_in[indeks_wersu_pierwszego])
        )
    ))
print(len(x))
print(x[0].shape)
print(x[0])

5959
torch.Size([617])
tensor([-3.1409e-02,  4.2919e-02, -1.4236e-02,  6.2288e-02, -3.2497e-02,
        -5.3290e-02,  4.7686e-02,  7.7745e-02, -2.0447e-02,  2.8347e-02,
         1.3510e-02, -2.3332e-01,  8.9271e-04,  4.0544e-02,  9.2784e-05,
        -1.1740e-02, -1.6238e-02, -4.7785e-02, -8.7547e-02,  6.0501e-02,
        -1.7588e-02, -4.3948e-03, -3.1034e-02, -8.8176e-03,  3.8507e-02,
        -5.6918e-02,  6.8194e-02,  7.5235e-03,  6.6778e-03,  2.0831e-02,
         9.5349e-04,  4.5033e-02, -9.4392e-03, -3.2470e-02, -3.5810e-02,
        -2.1215e-02, -2.9089e-02,  3.8043e-02, -2.6267e-02,  5.2310e-02,
        -6.3633e-02,  4.2117e-02,  1.7834e-02, -5.5019e-02, -7.9315e-02,
         8.2654e-04, -1.0802e-02,  1.8213e-02,  6.5130e-02, -7.6177e-03,
        -3.8167e-02,  5.3484e-02,  3.5490e-02,  2.7366e-02, -3.0560e-02,
        -7.8364e-02, -3.3920e-02,  7.5826e-03, -1.6268e-02,  1.9344e-02,
         3.4404e-02,  1.1855e-02, -3.5319e-02, -1.1730e-02,  6.7642e-02,
         3.7650e-04,  1.9837

### Tensory - reprezentacje drugich wersów wierszy treningowych.

In [74]:
y = []
for indeks_wersu_pierwszego in range(len(zanurzenia_treningowe_out)):
    y.append(
        torch.cat(
        (
            zanurzenia_treningowe_out[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_treningowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_treningowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_treningowe_out[indeks_wersu_pierwszego])
        )
    )
    )
print(len(y))
print(y[0].shape)
print(y[0])

5959
torch.Size([617])
tensor([ 2.4096e-02,  7.3348e-02, -8.4988e-03,  2.1168e-02, -5.1689e-02,
        -3.5376e-04,  4.7075e-02,  2.5451e-02,  3.5129e-02,  4.6819e-02,
         6.8763e-02, -2.2109e-01, -2.9449e-02,  5.0597e-02, -2.5865e-02,
        -9.3008e-03,  2.8629e-02, -6.2801e-02, -6.8237e-02, -5.9068e-02,
         2.1109e-02, -3.3667e-02, -3.0538e-02,  1.0535e-01,  3.0778e-02,
        -2.6921e-02, -4.7817e-03,  2.0352e-02, -6.7792e-02,  6.7208e-02,
         1.7218e-02,  1.9034e-02, -5.1180e-02, -1.4875e-02, -1.5020e-02,
        -1.2319e-02, -6.5349e-02,  4.0683e-02,  5.6421e-02, -2.2507e-02,
        -2.5330e-02,  4.9632e-02,  5.9727e-02,  9.1537e-03, -2.7953e-02,
        -4.3726e-02, -3.3593e-02,  1.8592e-02,  1.5352e-03, -9.2273e-03,
        -6.5650e-02,  3.0612e-02, -6.9992e-02, -2.7435e-02,  2.9220e-02,
        -3.2722e-02, -3.1333e-02,  1.2232e-02, -6.3038e-02,  6.2572e-04,
         2.0118e-02, -4.7327e-02, -4.6759e-02,  1.6298e-02,  2.4694e-02,
        -1.5708e-02, -1.7262

## Wejście do sieci neuronowej.
### Odpowiadające sobie wersy i kilka losowo dobranych nieodpowiadających sobie wersów.

In [75]:
from random import sample
X = []
Y = []
for indeks_wersu_drugiego in range(len(x)):
    indeksy = sample(range(len(y)), 3)
    if indeks_wersu_drugiego not in indeksy:
        indeksy[0] = indeks_wersu_drugiego
    for k in indeksy:
        X.append(
            torch.cat(
                (x[indeks_wersu_drugiego], y[k])
            )
        )
        if indeks_wersu_drugiego==k:
            Y.append(1)
        else:
            Y.append(0)

print(len(X))
print(X[0])
print(len(Y))
print(Y[0])

17877
tensor([-0.0314,  0.0429, -0.0142,  ...,  0.0000,  0.0000,  0.0000])
17877
1


## Modele sklearn.

In [76]:
from sklearn.neural_network import MLPClassifier
klasyfikator = MLPClassifier()   # activation="tanh"

klasyfikator.fit(X, Y)

MLPClassifier()

In [77]:
from sklearn.neural_network import MLPRegressor
regresor = MLPRegressor()   # activation="tanh"

regresor.fit(X, Y)

MLPRegressor()

### Początki, końcówki i tony wierszy testowych.

In [78]:
print(len(testowe["in"]))
print(testowe["in"][0])
print(testowe["out"][0])

liczba_wejscia = 35

poczatki_testowe_in, konce_testowe_in, tony_testowe_in = poczatki_konce_tony_dla_zdan(testowe["in"], liczba_wejscia)
poczatki_testowe_out, konce_testowe_out, tony_testowe_out = poczatki_konce_tony_dla_zdan(testowe["out"], liczba_wejscia)

print(len(poczatki_testowe_in))
print(poczatki_testowe_in[0])
print(konce_testowe_in[0])
print(tony_testowe_in[0])
print(poczatki_testowe_out[0])
print(konce_testowe_out[0])
print(tony_testowe_out[0])

1490
林霭渐浓迷古寺
尘烟已远隐青山
1490
[ 8 22 12  7  3  9 21  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[25 12 21 34  1  2  1  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[2 3 4 2 2 3 4 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
[16 22 22 22 22 13 17  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[24 21  1 23 25 32 20  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[2 1 3 3 3 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


### Zanurzenia BAAI wierszy testowych.

In [79]:
testowe_in_lista = testowe["in"].tolist()
testowe_out_lista = testowe["out"].tolist()

print(len(testowe_in_lista))
print(testowe_in_lista[0])
print(testowe_out_lista[0])

zanurzenia_testowe_in = zanurzenia_zdan(testowe_in_lista)
zanurzenia_testowe_out = zanurzenia_zdan(testowe_out_lista)

print(zanurzenia_testowe_in.shape)
print(zanurzenia_testowe_in[0])
print(zanurzenia_testowe_out[0])

1490
林霭渐浓迷古寺
尘烟已远隐青山
torch.Size([1490, 512])
tensor([-0.0803, -0.0044, -0.0786, -0.0128,  0.0160, -0.0353,  0.0014,  0.0223,
         0.0380, -0.0011,  0.0339, -0.2229,  0.0089,  0.0073, -0.0201,  0.0610,
        -0.0445, -0.0449, -0.0055, -0.0014, -0.0261, -0.0536, -0.0592, -0.0063,
         0.0381, -0.0866,  0.0715,  0.0058, -0.0275,  0.0164,  0.0154,  0.0230,
        -0.0277,  0.0550,  0.0030,  0.0233, -0.0007,  0.0052, -0.1081, -0.0225,
         0.0060,  0.0156,  0.0174, -0.0953, -0.0445, -0.0736,  0.0245,  0.0071,
        -0.0047, -0.0154,  0.0251,  0.0371,  0.0372,  0.0557,  0.0354,  0.0049,
        -0.0377,  0.0925, -0.0479,  0.0592, -0.0294, -0.0117, -0.0099, -0.0365,
        -0.0016,  0.0338,  0.0182,  0.0122, -0.0254,  0.0362,  0.0191, -0.0080,
        -0.0086, -0.0128, -0.0514, -0.0405, -0.0103,  0.0150, -0.0543, -0.0259,
         0.0189, -0.0283,  0.0074,  0.0298,  0.0197, -0.0688,  0.0169,  0.0327,
         0.0889, -0.0453,  0.0061, -0.0504,  0.0300,  0.0526,  0.0672,  0.0

### Tensory - reprezentacje pierwszych wersów wierszy testowych.

In [80]:
x_test = []
for indeks_wersu_pierwszego in range(len(zanurzenia_testowe_in)):
    x_test.append(torch.cat(
        (
            zanurzenia_testowe_in[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_testowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_testowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_testowe_in[indeks_wersu_pierwszego])
        )
    ))
print(len(x_test))
print(x_test[0].shape)
print(x_test[0])

1490
torch.Size([617])
tensor([-8.0259e-02, -4.3918e-03, -7.8638e-02, -1.2816e-02,  1.5959e-02,
        -3.5314e-02,  1.3728e-03,  2.2271e-02,  3.7977e-02, -1.1226e-03,
         3.3940e-02, -2.2293e-01,  8.9278e-03,  7.3494e-03, -2.0129e-02,
         6.0954e-02, -4.4464e-02, -4.4885e-02, -5.4901e-03, -1.3792e-03,
        -2.6079e-02, -5.3571e-02, -5.9173e-02, -6.3475e-03,  3.8071e-02,
        -8.6587e-02,  7.1489e-02,  5.7802e-03, -2.7479e-02,  1.6377e-02,
         1.5447e-02,  2.3025e-02, -2.7736e-02,  5.4993e-02,  3.0404e-03,
         2.3296e-02, -7.4090e-04,  5.2373e-03, -1.0805e-01, -2.2483e-02,
         5.9799e-03,  1.5623e-02,  1.7414e-02, -9.5345e-02, -4.4511e-02,
        -7.3634e-02,  2.4519e-02,  7.1082e-03, -4.7360e-03, -1.5421e-02,
         2.5125e-02,  3.7092e-02,  3.7218e-02,  5.5716e-02,  3.5407e-02,
         4.8798e-03, -3.7684e-02,  9.2484e-02, -4.7923e-02,  5.9173e-02,
        -2.9434e-02, -1.1721e-02, -9.8530e-03, -3.6479e-02, -1.6005e-03,
         3.3847e-02,  1.8198

### Tensory - reprezentacje drugich wersów wierszy testowych.

In [81]:
y_test = []
for indeks_wersu_pierwszego in range(len(zanurzenia_testowe_out)):
    y_test.append(
        torch.cat(
        (
            zanurzenia_testowe_out[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_testowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_testowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_testowe_out[indeks_wersu_pierwszego])
        )
    )
    )
print(len(y_test))
print(y_test[0].shape)
print(y_test[0])

1490
torch.Size([617])
tensor([-4.2662e-02, -3.1708e-02, -5.6512e-02,  4.0084e-02, -3.8748e-02,
         9.6097e-03,  4.7008e-02,  7.5668e-02, -1.3552e-02,  1.1450e-02,
         7.6131e-02, -2.4726e-01, -2.2119e-02, -3.7263e-02, -1.6699e-03,
        -2.8011e-03, -7.1475e-03,  1.0944e-02,  1.0504e-02, -1.9638e-02,
         3.1485e-02, -6.9084e-03, -2.0084e-02, -2.8139e-02, -2.1698e-02,
        -4.5725e-02,  6.2876e-02, -2.4744e-02, -5.4077e-02,  1.1777e-02,
         3.2030e-02, -6.9665e-03,  1.5294e-02, -8.0923e-02,  2.8682e-02,
         6.8040e-03, -3.3103e-03,  2.6560e-02, -6.0841e-02,  2.1151e-03,
        -3.2793e-02,  1.4114e-02, -3.0558e-02, -6.7261e-02, -7.8080e-02,
        -5.6005e-02, -2.4466e-02,  3.1131e-02,  1.2249e-02, -2.6226e-02,
         5.6157e-03, -1.4219e-02,  6.1117e-02,  8.7854e-02,  3.2294e-02,
        -7.5786e-02, -3.8687e-03,  5.8290e-02, -1.8115e-02,  9.2157e-03,
        -1.9775e-02, -1.4765e-02, -8.1864e-02, -5.2147e-02, -3.3906e-02,
         4.7297e-02,  1.7286

## Wejście do sieci neuronowej.

In [82]:
X_test = []
Y_test = []
for indeks_wersu_drugiego in range(len(x_test)):
    indeksy = sample(range(len(y_test)), 3)
    if indeks_wersu_drugiego not in indeksy:
        indeksy[0] = indeks_wersu_drugiego
    for k in indeksy:
        X_test.append(
            torch.cat(
                (x_test[indeks_wersu_drugiego], y_test[k])
            )
        )
        if indeks_wersu_drugiego==k:
            Y_test.append(1)
        else:
            Y_test.append(0)

print(len(X_test))
print(X_test[0])
print(len(Y_test))
print(Y_test[0])

4470
tensor([-0.0803, -0.0044, -0.0786,  ...,  0.0000,  0.0000,  0.0000])
4470
1


## Przewidywania sieci neuronowych.

In [83]:
przewidywania_klasyfikatora = klasyfikator.predict(X_test)

In [84]:
przewidywania_regresora = regresor.predict(X_test)
print(numpy.min(przewidywania_regresora),numpy.max(przewidywania_regresora),numpy.mean(przewidywania_regresora),numpy.median(przewidywania_regresora))

-1.250942997983307 2.1043229513866173 0.33757049502639574 0.28136695410859397


### Dokładność na przygotowanych danych testowych.

In [85]:
### MLPClassifier

licznik = 0
mianownik = 0
for indeks_wersu_pierwszego in range(len(przewidywania_klasyfikatora)):
    mianownik+=1
    if przewidywania_klasyfikatora[indeks_wersu_pierwszego]==Y_test[indeks_wersu_pierwszego]:
        licznik+=1

print(licznik/mianownik*1.0)

0.8402684563758389


In [86]:
### MLPRegressor

# Dopasowanie powyżej 0.5
licznik = 0
mianownik = 0
for indeks_wersu_pierwszego in range(len(przewidywania_regresora)):
    mianownik+=1
    if Y_test[indeks_wersu_pierwszego]==1 and przewidywania_regresora[indeks_wersu_pierwszego]>0.5:
        licznik+=1
    elif Y_test[indeks_wersu_pierwszego]==0 and przewidywania_regresora[indeks_wersu_pierwszego]<0.5:
        licznik+=1

print(licznik/mianownik*1.0)

#Dopasowanie powyżej 0.9
licznik = 0
mianownik = 0
for indeks_wersu_pierwszego in range(len(przewidywania_regresora)):
    mianownik+=1
    if Y_test[indeks_wersu_pierwszego]==1 and przewidywania_regresora[indeks_wersu_pierwszego]>0.9:
        licznik+=1
    elif Y_test[indeks_wersu_pierwszego]==0 and przewidywania_regresora[indeks_wersu_pierwszego]<0.9:
        licznik+=1

print(licznik/mianownik*1.0)

0.8217002237136465
0.7507829977628635


## Metryka oceniająca proponowanie przez model drugiego wersu.
### Jeżeli wśród propozycji nie ma spodziewanego poprawnego wersu, metryka przyjmuje minimalną wartość 0,0.
### Im mniej błędnych propozycji , tym wyższy wynik metryki.
### Jeżeli model proponuje tylko jeden wers i jest on poprawny, metryka przyjmuje maksymalną wartość 1,0.

In [87]:
def jagosz_score(spodziewany_wers,proponowane_wersy):
    if spodziewany_wers in proponowane_wersy:
        licznik = 1
    else:
        licznik = 0
    mianownik = len(proponowane_wersy)
    if mianownik==0:
        mianownik=1
    return licznik/mianownik*1.0

### Wersja metryki dla całego zbioru.

In [88]:
def jagosz_score_dla_zbioru(krotki):
    licznik = 0
    mianownik = 0

    for k in krotki:
        spodziewany_wers = k[0]
        proponowane_wersy = k[1]
        if spodziewany_wers in proponowane_wersy:
            licznik += 1
        mianownik += len(proponowane_wersy)

    if mianownik==0:
        return 0
    else:
        return licznik/mianownik*1.0

In [89]:
wybrane_dane_testowe = sample(range(len(x_test)),10)

## MLPClassifier
### Proponuje wszystkie wersy, dla których ocena modelu to 1.

In [90]:
for indeks_wersu_pierwszego in wybrane_dane_testowe:
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    print("wers pierwszy:\t\t", wers_pierwszy)
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]
    print("poprawny wers drugi:\t", poprawny_wers_drugi)
    print()

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        if klasyfikator.predict([wejscie_do_MLP])[0] == 1:
            mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)

    proponowane_wersy = [testowe["out"][i] for i in mozliwe_indeksy_wersu_drugiego]
    print("proponowane drugie wersy:", proponowane_wersy)
    print("czy poprawny wers jest pośród proponowanych wersów?:", poprawny_wers_drugi in proponowane_wersy)
    print("liczba proponowanych wersów:", len(proponowane_wersy))
    print()

    print("wynik przyjętej metryki:", jagosz_score(poprawny_wers_drugi, proponowane_wersy))
    print()
    print("-"*50)
    print()

wers pierwszy:		 花好月圆涵画意
poprawny wers drugi:	 年丰人寿沁诗声

proponowane drugie wersy: ['谁将片语问何求', '他乡月好俺思亲', '三杯白酒乐成仙', '峰平径长难藏景', '海深寻秘展雄才', '青山醉向一樽横', '好同蝉窟映三潭', '万般幻态杳随风', '须先百忍学张公', '珠帘难掩月多情', '莺燕对舞艳阳天', '青山四面纳千流', '一心二用两头空', '闲庭信步哼欢歌', '雾里青山画屏开', '殷殷老叶护花红', '偶观雨燕栖寒檐', '满头霜雪和新梅', '居身常抱玉壶清', '竹林满山景隽幽', '一腔热血死难消', '清风两袖带回家', '日月同辉光景嫣', '三阳开泰颂廉明', '小楼吹砌玉生寒', '锦葵昂面为迎光', '浮沉历尽许由谁', '闹中取静看擂台', '早将秋韵入诗怀', '满身花影倩人扶', '千杯浊酒醉恒长', '心牵雨骤夜归人', '与君同作太平人', '青灯久作故人看', '猴腾广宇绽琼花', '好留明月九千秋', '花狎春云露搅和', '三联书韵醉今生', '风临荷盏窃清香', '花好月圆夜长明', '河清海晏让人迷', '心宽纳海老夫能', '扬鞭跃马马行空', '鹰翔蓝宇戏搏云', '甘棠播爱岁流金', '胸中消尽是非心', '弄潮帆影港城新', '英年奋进惜时光', '堤前柳浪露春光', '故人书自日边来', '文联叶问斩妖魔', '梅香葱岭缀长虹', '万般气象壮龙年', '催开玉蕊艳无边', '清塘浴月鹤逐风', '卷帘烧烛看梅花', '圆缺朗月也浮名', '思亲情愫贯通篇', '梧桐叶上得秋声', '一杯浊酒两篇诗', '动动脑筋动静无', '新朋正续进行时', '一指清凉尽染秋', '日移松影过禅床', '无田有业不为贫', '一溪柳绿到谁家', '风临柳榭露春心', '西湖乡梦约谁寻', '远山终日送余霞', '纵情狂乱毁根基', '笛声浅扣暗推窗', '一川杨柳笼和风', '洗出芙蓉九点青', '半空摇晃寻常仁', '追求亮丽美人图', '雪融春到春融雪', '常将劲节负秋霜', '国持德政著宏篇', '千般爱意眼中留', '绿水卧听新月明', '兰心未老梦如初', '英雄力困也求人', '且由明月洗尘心', '夜灯勤

## MLPRegressor
### Proponuje wszystkie wersy, dla których ocena modelu jest większa niż 0,9.

In [91]:
for indeks_wersu_pierwszego in wybrane_dane_testowe:
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    print("wers pierwszy:\t\t", wers_pierwszy)
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]
    print("poprawny wers drugi:\t", poprawny_wers_drugi)
    print()

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        wartosci_przewidywan_wersu_drugiego.append(regresor.predict([wejscie_do_MLP])[0])

    pom_df = pandas.DataFrame({"indeks":mozliwe_indeksy_wersu_drugiego,"wartosc":wartosci_przewidywan_wersu_drugiego})
    proponowane_wersy = [testowe["out"][i] for i in pom_df["indeks"] if pom_df["wartosc"][i]>=0.9]

    print("proponowane drugie wersy:", proponowane_wersy)
    print("czy poprawny wers jest pośród proponowanych wersów?:", poprawny_wers_drugi in proponowane_wersy)
    print("liczba proponowanych wersów:", len(proponowane_wersy))
    print()

    print("wynik przyjętej metryki:", jagosz_score(poprawny_wers_drugi, proponowane_wersy))
    if (len(proponowane_wersy)<1 or len(proponowane_wersy)>5):
        print("wyjaśnienie - największe wartości przewidywań")
        print(pom_df.nlargest(len(proponowane_wersy)+1, "wartosc"))
    print()
    print("-"*50)
    print()

wers pierwszy:		 花好月圆涵画意
poprawny wers drugi:	 年丰人寿沁诗声

proponowane drugie wersy: ['尘烟已远隐青山', '而今华夏振雄风', '他乡月好俺思亲', '火山光灿地遭殃', '三杯白酒乐成仙', '峰平径长难藏景', '海深寻秘展雄才', '青山醉向一樽横', '好同蝉窟映三潭', '铮铮梅蕾半含春', '莺燕对舞艳阳天', '一心二用两头空', '闲庭信步哼欢歌', '偶观雨燕栖寒檐', '居身常抱玉壶清', '清风两袖带回家', '三阳开泰颂廉明', '小楼吹砌玉生寒', '锦葵昂面为迎光', '看三国志欲何为', '闹中取静看擂台', '与君同作太平人', '青灯久作故人看', '猴腾广宇绽琼花', '好留明月九千秋', '风临荷盏窃清香', '古人异代不同时', '弄潮帆影港城新', '堤前柳浪露春光', '春江柳线乱弹琴', '梅香葱岭缀长虹', '仙人指路点迷津', '梧桐叶上得秋声', '无田有业不为贫', '一溪柳绿到谁家', '风临柳榭露春心', '俨然天竺古先生', '武夷阳羡品俱馨', '远山终日送余霞', '笛声浅扣暗推窗', '一川杨柳笼和风', '半空摇晃寻常仁', '追求亮丽美人图', '雪融春到春融雪', '常将劲节负秋霜', '善男信女拜观音', '劈开天地定人伦', '举杯邀月到凡尘', '伤心羁旅断愁肠', '夜灯勤礼塔中仙', '赋浓夏盛寓秋实', '牢盆给费利官民', '飞鸿远浦一时惊', '蛇听燕语颂春光', '清泉有趣自通融', '游春岂料梦成真', '年丰人寿沁诗声', '霜飞两鬓孔明灯', '不言第一海胸襟', '乌啼古树惹乡愁', '难经何必借炎黄', '子孙常读未烧书', '情凝大地重如山', '长将远景引天边', '有悲寒户落新愁', '满腔忧愤铸诗魂', '万般殷切候佳音', '行吟战马啸征尘', '何堪永夜漏更寒', '荷描夏画日钤章', '漫天风语绕苍穹', '花贴幼子悦童心', '红旗漫卷息狼烟', '四行热泪洒苍颜', '人间重义树新风', '一言九鼎定心神', '春风念字到青青', '观光农业载风情', '钻杆穿地唱欢歌', '再将粉黛沁于宣', '秉公执法树廉风', '当惊阁老好风光', '梅花傲雪迓长春', '出门去

## MLPClassifier
### Przyjęta metryka dla 1/100 zbioru testowego.

In [92]:
krotki = []
czesc_zbioru_testowego, _ = train_test_split(x_test,test_size=0.95,random_state=42)
for indeks_wersu_pierwszego in range(len(czesc_zbioru_testowego)):
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        if klasyfikator.predict([wejscie_do_MLP])[0] == 1:
            mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)

    proponowane_wersy = [testowe["out"][i] for i in mozliwe_indeksy_wersu_drugiego]

    krotki.append((poprawny_wers_drugi,proponowane_wersy))

print(jagosz_score_dla_zbioru(krotki))

0.0005942200059422001


### Średnia metryk dla 1/100 zbioru testowego.

In [93]:
jagosz_scores=[]
for indeks_wersu_pierwszego in range(len(czesc_zbioru_testowego)):
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        if klasyfikator.predict([wejscie_do_MLP])[0] == 1:
            mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)

    proponowane_wersy = [testowe["out"][i] for i in mozliwe_indeksy_wersu_drugiego]

    jagosz_scores.append(jagosz_score(poprawny_wers_drugi,proponowane_wersy))

print(numpy.mean(jagosz_scores))

0.0005963998131847716


## MLPClassifier
### Przyjęta metryka dla 1/100 zbioru testowego.

In [98]:
krotki = []
for indeks_wersu_pierwszego in range(len(czesc_zbioru_testowego)):
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        wartosci_przewidywan_wersu_drugiego.append(regresor.predict([wejscie_do_MLP])[0])

    pom_df = pandas.DataFrame({"indeks":mozliwe_indeksy_wersu_drugiego,"wartosc":wartosci_przewidywan_wersu_drugiego})
    proponowane_wersy = [testowe["out"][i] for i in pom_df["indeks"] if pom_df["wartosc"][i]>=0.9]

    krotki.append((poprawny_wers_drugi,proponowane_wersy))

print(jagosz_score_dla_zbioru(krotki))

0.005119117936601693


### Średnia metryk dla 1/100 zbioru testowego.

In [99]:
jagosz_scores=[]
for indeks_wersu_pierwszego in range(len(czesc_zbioru_testowego)):
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        wartosci_przewidywan_wersu_drugiego.append(regresor.predict([wejscie_do_MLP])[0])

    pom_df = pandas.DataFrame({"indeks":mozliwe_indeksy_wersu_drugiego,"wartosc":wartosci_przewidywan_wersu_drugiego})
    proponowane_wersy = [testowe["out"][i] for i in pom_df["indeks"] if pom_df["wartosc"][i]>=0.9]

    jagosz_scores.append(jagosz_score(poprawny_wers_drugi,proponowane_wersy))

print(numpy.mean(jagosz_scores))

0.011362779457775134


In [97]:
print(len(czesc_zbioru_testowego))

74
